In [1]:
import warnings

warnings.filterwarnings("ignore")

from transformers import pipeline

# pipeline are used for inference

sequence_classifier = pipeline("sentiment-analysis")

sequence_classifier("I love you")





No model was supplied, defaulted to distilbert/distilbert-base-uncased-finetuned-sst-2-english and revision 714eb0f (https://huggingface.co/distilbert/distilbert-base-uncased-finetuned-sst-2-english).
Using a pipeline without specifying a model name and revision in production is not recommended.
Device set to use mps:0


[{'label': 'POSITIVE', 'score': 0.9998656511306763}]

In [2]:
my_texts = ["I love you", "I hate you"]

sequence_classifier(my_texts)

[{'label': 'POSITIVE', 'score': 0.9998656511306763},
 {'label': 'NEGATIVE', 'score': 0.9991129040718079}]

In [3]:
# Speech to text - automatic speech recognition

speech_recognizer = pipeline("automatic-speech-recognition", model= "facebook/wav2vec2-base-960h")

Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-base-960h and are newly initialized: ['wav2vec2.masked_spec_embed']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Device set to use mps:0


In [4]:
from datasets import load_dataset, Audio

dataset = load_dataset("speechbrain/LargeScaleASR", "small" ,split="dev", streaming=True)

dataset

IterableDataset({
    features: ['ID', 'duration', 'wav', 'spk_id', 'sex', 'text'],
    num_shards: 6
})

In [5]:
# dataset = dataset.cast_column("audio", Audio(sampling_rate=speech_recognizer.feature_extractor.sampling_rate))

In [6]:
dataset = list(dataset.take(4))
dataset

[{'ID': '20170703-0900-PLENARY-16-en_20170703-17:34:14_15',
  'duration': 9.399937629699707,
  'wav': {'bytes': b'RIFFD\x97\x04\x00WAVEfmt \x10\x00\x00\x00\x01\x00\x01\x00\x80>\x00\x00\x00}\x00\x00\x02\x00\x10\x00LIST\x1a\x00\x00\x00INFOISFT\r\x00\x00\x00Lavf61.1.100\x00\x00data\xfe\x96\x04\x00\xbd\xff\x9b\xff\xf7\xff5\x00\xf1\xff\xa9\xff\r\x00W\x00\xd3\xff\x9e\xff\x08\x00P\x00\xd2\xff\x99\xff\x15\x00.\x00\xf8\xff\xef\xff\x1c\x00\xf2\xff\xad\xff\xc6\xff5\x00J\x00\xda\xff\x95\xff\x03\x00b\x00/\x00\xb3\xff\xa3\xff\xea\xff$\x00\x08\x00\xd5\xff\x04\x00<\x00\x06\x00\xb5\xff\xfc\xffO\x00\xf2\xff\xb1\xff6\x00Q\x00\xe7\xff\xe4\xffW\x00N\x00\xee\xff\xc6\xff\x1d\x00p\x00\x14\x00\x8c\xff\xb5\xffM\x00z\x00\xef\xff\x90\xff\xe8\xff[\x00G\x00\xe1\xff\x9e\xff\xd6\xff6\x00(\x00\xfd\xff\n\x00!\x00\xfc\xff\xf8\xff\x01\x00\r\x00\xdf\xff\xd1\xff1\x00@\x00\x1d\x00\xe7\xff\xd3\xff\xed\xff\x06\x00\xf3\xff\xf6\xff\x00\x00\xe1\xff\xfa\xff \x00\x1c\x00\x0f\x00\xf0\xff\xf3\xff\xfa\xff\xcf\xff\xe0\xff1\x00@\x00\x0

In [7]:
from datasets import Dataset

dataset = Dataset.from_list(dataset)

In [8]:
dataset

Dataset({
    features: ['ID', 'duration', 'wav', 'spk_id', 'sex', 'text'],
    num_rows: 4
})

In [9]:
dataset = dataset.cast_column("wav", Audio(sampling_rate=speech_recognizer.feature_extractor.sampling_rate))

In [10]:
dataset[0]["wav"]

{'path': '20170703-0900-PLENARY-16-en_20170703-17:34:14_15.wav',
 'array': array([-0.00204468, -0.00308228, -0.00027466, ...,  0.00076294,
         0.00073242,  0.00073242]),
 'sampling_rate': 16000}

In [11]:
speech_recognizer.feature_extractor.sampling_rate

16000

In [15]:
dataset[0]["wav"]

{'path': '20170703-0900-PLENARY-16-en_20170703-17:34:14_15.wav',
 'array': array([-0.00204468, -0.00308228, -0.00027466, ...,  0.00076294,
         0.00073242,  0.00073242]),
 'sampling_rate': 16000}

In [17]:
result = speech_recognizer(dataset[:4]["wav"])
print([d["text"] for d in result])

['THESE ARE REFORMED THAT WILL DISCIPLINE AND CONSTRAIN THE EXERCISE OF POWER BY THE GOVERNMENT AND ANY OTHER ECONOMICAL POLITICAL ACTOR FOR GENERATIONS TO COME', 'I AM VERY GRATEFUL THAT WE ARE WHERE WE ARE NOW I AM INDEED YOU CRANE NEEDS THIS THE PORT AND IT DESERVES THIS THEPORT AND I THINK IT IS VERY APPROPRIATE TO HAVE THIS THE NEXT PROGRAMME NOW', "THERE ISN'T THAT IS CITIZENSHIPD BY IDENTIFICATION INTEGRATION MERIT BELIEF IN WHAT WE STAND FOR AS NATIONS AND ASEUROPEAN UNION", 'STONIA HAS CHOSEN FOURMAIN OBJECTIVES FOR THE NEXT SIXT MONTHS']


In [18]:
# Success , keep trying man